![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo I 2019 Cobertura de Plano de Saúde

## Bibliotecas Utilizadas

In [2]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [3]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

[1] 293725    682

## Definição do peso e filtragem de respondentes do questionário

In [4]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2019.1<- <Coloque aqui o nome do arquivo RDATA> %>% mutate(peso_moradores=((V00281*279382/209589607))) 
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_moradores))
summary(pns2019.1$peso_moradores)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.01046  0.31515  0.58914  1.00000  1.16920 39.99838 

## Criação de variáveis dos indicadores

In [5]:
#Desfechos - Indicadores

#Posse de plano de saúde médico ou odontológico particular - I001P
pns2019.1 <- pns2019.1 %>% mutate(I001P = ifelse(I00101==2 & I00102==2,2,
                                          ifelse(I00101==1 | I00102==1,1,2)))                                         
pns2019.1$I001P<-factor(pns2019.1$I001P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$I001P)


#Posse de plano de saúde médico particular  - I002P
pns2019.1 <- pns2019.1 %>% mutate(I002P= ifelse(I00102==1, 1,0))
pns2019.1$I002P<-factor(pns2019.1$I002P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2019.1$I002P)

#Posse de plano de saúde odontológico particular  - I003P
pns2019.1 <- pns2019.1 %>% mutate(I003P= ifelse(I00101 ==1, 1,0))
pns2019.1$I003P<-factor(pns2019.1$I003P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2019.1$I003P)




Sim    Não 
 65118 214264

Sim    Não 
 58597 220785

Sim    Não 
 31511 247871

## Definições de abrangências

### Situação urbana ou rural

In [6]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Situação_Urbano_Rural=V0026)
pns2019.1$Situação_Urbano_Rural<-factor(pns2019.1$Situação_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2019.1$Situação_Urbano_Rural)

Urbano  Rural 
212286  67096

### Sexo

In [7]:
#Sexo
pns2019.1 <- pns2019.1 %>% rename(Sexo=C006)
pns2019.1$Sexo<-factor(pns2019.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2019.1$Sexo)

Masculino  Feminino 
   134442    144940

### UF

In [8]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federação=V0001)
pns2019.1$Unidades_da_Federação<-factor(pns2019.1$Unidades_da_Federação, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federação)

Rondônia                Acre            Amazonas             Roraima 
               7037                7808               12642                7995 
               Pará               Amapá           Tocantins            Maranhão 
              13475                6363                6127               17327 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               8745               14157                9472                9652 
         Pernambuco             Alagoas             Sergipe               Bahia 
              11934                9947                7803               10516 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
              14831               10078               13909               17522 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
              11237               10123                9878                8350 
        Mato Grosso               Goiás    Distrito Federal 
               7291                8003                7160

### Grandes Regiões

In [9]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federação, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       61447        99553        56340        31238        30804

### Capital

In [10]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federação,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          7037           7808          12642           7995          13475 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          6363           6127          17327           8745          14157 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          9472           9652          11934           9947           7803 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
         10516          14831          10078          13909          17522 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
         11237          10123           9878           8350           7291 
       Goiânia       Brasília 
          8003           7160

### Faixa Etária

In [11]:
#Faixas Etárias
pns2019.1 <- pns2019.1 %>% mutate(faixa_idade = ifelse(C008<=0,1, 
                        ifelse(C008%in% 1:4, 2, 
                        ifelse(C008%in% 5:14, 3,
                        ifelse(C008%in% 15:24, 4,
                        ifelse(C008%in% 25:34, 5,
                        ifelse(C008%in% 35:44, 6,
                        ifelse(C008%in% 45:59, 7,8))))))))

pns2019.1$faixa_idade<-factor(pns2019.1$faixa_idade, levels=c(1,2,3,4,5,6,7,8), labels=c("Menor de 1 ano","1 a 4 anos","5 a 14 anos","15 a 24 anos","25 a 34 anos","35 a 44 anos","45 a 59 anos","60 anos ou mais"))
summary(pns2019.1$faixa_idade) 

Menor de 1 ano      1 a 4 anos     5 a 14 anos    15 a 24 anos    25 a 34 anos 
           3349           14438           40500           43827           39854 
   35 a 44 anos    45 a 59 anos 60 anos ou mais 
          41460           52400           43554

### Raça

In [12]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 99019  28304 148273   3786

### Renda per capita

In [13]:
#Rendimento domiciliar per capita

pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4,
                        ifelse(VDF004==9,"NA",5))))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       91898        81830        61643        19369        24470          172

## Criando indicadores

### Filtrando base de indicadores

In [14]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019survey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_moradores", "I001P","I002P","I003P", "V0031","C009","VDF004",
                                     "Situação_Urbano_Rural","Sexo","Unidades_da_Federação", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita")
summary(pns2019survey)

     V0024            UPA_PNS          peso_moradores     I001P       
 Min.   :1110011   Min.   :110000016   Min.   : 0.01046   Sim: 65118  
 1st Qu.:2152011   1st Qu.:210048674   1st Qu.: 0.31515   Não:214264  
 Median :2752010   Median :270027654   Median : 0.58914               
 Mean   :2916319   Mean   :288513887   Mean   : 1.00000               
 3rd Qu.:3522011   3rd Qu.:350367169   3rd Qu.: 1.16920               
 Max.   :5310220   Max.   :530051067   Max.   :39.99838               
                                                                      
 I002P        I003P            V0031            C009           VDF004     
 Sim: 58597   Sim: 31511   Min.   :1.000   Min.   :1.000   Min.   :1.000  
 Não:220785   Não:247871   1st Qu.:1.000   1st Qu.:1.000   1st Qu.:2.000  
                           Median :2.000   Median :4.000   Median :3.000  
                           Mean   :2.608   Mean   :2.736   Mean   :3.197  
                           3rd Qu.:4.000   3rd Qu.:4.000 

### Exporta tabela filtrada com os dados específicos - Módulo I 2019

In [16]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019survey, file.path(diretorio_saida, "pns2019Isurvey.csv"))

### Cria plano amostral complexo

In [17]:
#survey design
desPNSI=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_moradores, nest=TRUE, data=pns2019survey)
desPNSIC=subset(desPNSI, V0031==1)
desPNSIR=subset(desPNSI, C009!=9)
desPNSIRE=subset(desPNSI, VDF004!=9)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [18]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [19]:
ListaIndicadores = c(~I001P,~I002P,~I003P)
ListaIndicadoresTexto = c("I001P","I002P","I003P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Situação_Urbano_Rural,~Unidades_da_Federação,~GrandesRegioes,~Capital)
ListaDominiosTexto = c("Sexo","raça","rend_per_capita","fx_idade","urb_rur","uf","região","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [20]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                  dataframe_indicador<-svyby(indicador , dominio , desPNSIC , svymean,vartype= c("ci","cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               #não possuiam dados suficientes para os dominios dos indicadores
               else if (ListaDominiosTexto[j]=="raça"){
                dataframe_indicador<-svyby(indicador , dominio , desPNSIR , svymean,vartype= c("ci","cv"))
                   }
               #Uso design do subconjunto para renda que exclui valores NULOS 
               else if (ListaDominiosTexto[j]=="rend_per_capita"){
                dataframe_indicador<-svyby(indicador , dominio , desPNSIRE , svymean,vartype= c("ci","cv"))
                   }
               #design geral para o subconjunto maior que 18 anos    
               else {
                   dataframe_indicador<-svyby(indicador , dominio , desPNSI , svymean,vartype= c("ci","cv"))
                 
               }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               dataframe_indicador<-data.frame(dataframe_indicador)
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Não","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }

}


#### Criando a tabela pela abrangência total

In [21]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [22]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        if(total == 'Capital'){
                       dataframe_indicador <- svymean(indicador,desPNSIC)
             }else{
                       dataframe_indicador <- svymean(indicador,desPNSI)
        }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}
    

#### Unindo tabela de indicadores e de totais

In [23]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [24]:
matrizIndicadores

abr_tipo        abr_nome        Ano  Indicador Sim       
Masculino       Sexo            Masculino       2019 I001P     0.27388650
Feminino        Sexo            Feminino        2019 I001P     0.29508554
Branca          raça            Branca          2019 I001P     0.38802339
Preta           raça            Preta           2019 I001P     0.21423604
Parda           raça            Parda           2019 I001P     0.20099362
Até 1/2 SM      rend_per_capita Até 1/2 SM      2019 I001P     0.05825318
1/2 até 1 SM    rend_per_capita 1/2 até 1 SM    2019 I001P     0.17653124
1 até 2 SM      rend_per_capita 1 até 2 SM      2019 I001P     0.35748528
2 até 3 SM      rend_per_capita 2 até 3 SM      2019 I001P     0.54822804
Mais de 3 SM    rend_per_capita Mais de 3 SM    2019 I001P     0.79230690
Menor de 1 ano  fx_idade        Menor de 1 ano  2019 I001P     0.27324375
1 a 4 anos      fx_idade        1 a 4 anos      2019 I001P     0.28148882
5 a 14 anos     fx_idade        5 a 14 anos     2019 I001P     0.25153348
15 a 24 anos    fx_idade        15 a 24 anos    2019 I001P     0.23409422
25 a 34 anos    fx_idade        25 a 34 anos    2019 I001P     0.29703277
35 a 44 anos    fx_idade        35 a 44 anos    2019 I001P     0.32592919
45 a 59 anos    fx_idade        45 a 59 anos    2019 I001P     0.29365128
60 anos ou mais fx_idade        60 anos ou mais 2019 I001P     0.30214641
Urbano          urb_rur         Urbano          2019 I001P     0.32162083
Rural           urb_rur         Rural           2019 I001P     0.07013919
Rondônia        uf              Rondônia        2019 I001P     0.13765773
Acre            uf              Acre            2019 I001P     0.09564527
Amazonas        uf              Amazonas        2019 I001P     0.16262579
Roraima         uf              Roraima         2019 I001P     0.08270107
Pará            uf              Pará            2019 I001P     0.15734934
Amapá           uf              Amapá           2019 I001P     0.12025701
Tocantins       uf              Tocantins       2019 I001P     0.13093836
Maranhão        uf              Maranhão        2019 I001P     0.06474890
Piauí           uf              Piauí           2019 I001P     0.16703997
Ceará           uf              Ceará           2019 I001P     0.18305157
⋮               ⋮               ⋮               ⋮    ⋮         ⋮         
Boa Vista2      capital         Boa Vista       2019 I003P     0.0517498 
Belém2          capital         Belém           2019 I003P     0.1957352 
Macapá2         capital         Macapá          2019 I003P     0.1030244 
Palmas2         capital         Palmas          2019 I003P     0.1174263 
São Luís2       capital         São Luís        2019 I003P     0.1162225 
Teresina2       capital         Teresina        2019 I003P     0.1244709 
Fortaleza2      capital         Fortaleza       2019 I003P     0.2386610 
Natal2          capital         Natal           2019 I003P     0.2055142 
João Pessoa2    capital         João Pessoa     2019 I003P     0.2426274 
Recife2         capital         Recife          2019 I003P     0.2525145 
Maceió2         capital         Maceió          2019 I003P     0.2105149 
Aracaju2        capital         Aracaju         2019 I003P     0.2508889 
Salvador2       capital         Salvador        2019 I003P     0.2518312 
Belo Horizonte2 capital         Belo Horizonte  2019 I003P     0.2232149 
Vitória2        capital         Vitória         2019 I003P     0.2442612 
Rio de Janeiro5 capital         Rio de Janeiro  2019 I003P     0.2424249 
São Paulo4      capital         São Paulo       2019 I003P     0.1725544 
Curitiba2       capital         Curitiba        2019 I003P     0.2715516 
Florianópolis2  capital         Florianópolis   2019 I003P     0.2169666 
Porto Alegre2   capital         Porto Alegre    2019 I003P     0.2402589 
Campo Grande2   capital         Campo Grande    2019 I003P     0.2287930 
Cuiabá2         capital         Cuiabá          2019 I003P     0.1168575 
Goiânia2        capi

#### Exportando tabela de indicadores calculados - Módulo I 2019

In [25]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2019I_R.csv"),sep = ";",dec = ",",row.names = FALSE)